# Clickstream Project

Your client `Kirana Store` is an E-commerce company. The company wants to focus on targeting the right customers  with the right products to increase overall revenue and conversion rate.

`Kirana Store` has provided you with the clickstream data on their website and wants you to tell them the answer to their queries. This will help them improve their understanding about their customers so that they can create better product personalization, marketing campaigns, advertisements, etc.

The data contains the following fields :-

- `webClientID` - Unique ID of browser for every system. (If a visitor is using multiple browsers on a system like Chrome, Safari, then there would be a different web clientid for each browser). 

- `VisitDateTime` - Date and time of visit.

- `ProductID` - Unique ID of product browsed/ clicked by the visitor.

- `Activity` - Type of activity can be browsing (`pageload`) or clicking (`click`) a product

- `device` - Information about the device used by visitor to visit the website
> - `Browser` - Browser used by visitor
> - `OS` - OS used by the visitor

- `user` - Information about registered user or users who have already signed up
> - `UserID` - Unique ID of the user
> - `City` - City of the user
> - `Country` - Country of the user

----
## Connecting to MongoDB

----

In [1]:
# Importing the required libraries
import pymongo
import pandas as pd
from datetime import datetime
import pprint as pp

# Does not allow pprint to sort the fields
pp.sorted = lambda x, key=None: x

In [2]:
# Connect to local MongoDB server
client = pymongo.MongoClient("mongodb://localhost:27017/")

In [3]:
# # Restore database
#!mongorestore C:\Users\dobby\Downloads\project

In [4]:
# Choose the database
db = client['project']

In [5]:
# Sample document
pp.pprint(
    db.clicks.find_one()
)

{'_id': ObjectId('60df1029ad74d9467c91a932'),
 'webClientID': 'WI100000244987',
 'VisitDateTime': datetime.datetime(2018, 5, 25, 4, 51, 14, 179000),
 'ProductID': 'Pr100037',
 'Activity': 'click',
 'device': {'Browser': 'Firefox', 'OS': 'Windows'},
 'user': {'City': 'Colombo', 'Country': 'Sri Lanka'}}


---
## Overiew of the data

----

Number of documents in the collection

In [6]:
# Count the total number of documents in the 'clicks' collection.
db.clicks.count_documents({})

6100000

---
Minimum date for which the records are present

In [7]:
# Find all documents in the 'clicks' collection and project only the 'VisitDateTime' field while excluding the '_id' field
#after sorting in ascending order and limiting the 1st element.
cur = db.clicks.find({}, {'VisitDateTime': 1, '_id': 0})\
               .sort([('VisitDateTime', pymongo.ASCENDING)])\
               .limit(1)
# Iterate through the cursor (containing one document, the earliest based on 'VisitDateTime') and print its content.
for doc in cur:
    pp.pprint(doc)

{'VisitDateTime': datetime.datetime(2018, 5, 7, 0, 0, 1, 190000)}


----
Maximum date  for which the records are present

In [8]:
# Find all documents in the 'clicks' collection and project only the 'VisitDateTime' field while excluding the '_id' field
#after sorting in descending order and limiting the 1st element.
cur = db.clicks.find({}, {'VisitDateTime': 1, '_id': 0})\
                   .sort([('VisitDateTime', pymongo.DESCENDING)])\
                   .limit(1)
# Iterate through the cursor (containing one document, the earliest based on 'VisitDateTime') and print its content.
for doc in cur:
    pp.pprint(doc)

{'VisitDateTime': datetime.datetime(2018, 5, 27, 23, 59, 59, 576000)}


----
Number of documents that have `user.UserID` field or number of users who have signed up on the website.

In [9]:
# Count the number of documents in the 'clicks' collection where the 'user.UserID' field exists.
len(list(db.clicks.find({'user.UserID': {'$exists': True}})))

602293

---
Unique signed up users in the complete data

In [10]:
# Count the number of distinct documents in the 'clicks' collection where the 'user.UserID' field exists.
len(db.clicks.find({'user.UserID': {'$exists': True}}).distinct('user.UserID'))

34050

---
Unique countries and cities

In [11]:
cur = db.clicks.aggregate([
    # Stage 1 - Match documents where both 'user.Country' and 'user.City' fields exist
    {
        '$match': {
            'user.Country': {'$exists': True},
            'user.City': {'$exists': True}
        }
    },
    # Stage 2 - Group documents by 'user.Country' and 'user.City'
    {
        '$group': {
            '_id': {
                'Country': '$user.Country',
                'City': '$user.City'
            }
        }
    },
    # Stage 3 - Sort the grouped data by 'Country' in ascending order (A-Z)
    {
        '$sort': {'_id.Country': 1}
    }
])

# Print the result for each document in the aggregation output
for doc in cur:
    pp.pprint(doc)


{'_id': {'Country': 'Afghanistan', 'City': 'Kabul'}}
{'_id': {'Country': 'Albania', 'City': 'Elbasan'}}
{'_id': {'Country': 'Albania', 'City': 'Korçë'}}
{'_id': {'Country': 'Albania', 'City': 'Durrës'}}
{'_id': {'Country': 'Albania', 'City': 'Lezhë'}}
{'_id': {'Country': 'Albania', 'City': 'Kosove'}}
{'_id': {'Country': 'Albania', 'City': 'Fier'}}
{'_id': {'Country': 'Albania', 'City': 'Yzberish'}}
{'_id': {'Country': 'Albania', 'City': 'Shkoder'}}
{'_id': {'Country': 'Albania', 'City': 'Tirana'}}
{'_id': {'Country': 'Algeria', 'City': 'Béjaïa'}}
{'_id': {'Country': 'Algeria', 'City': 'Mostaganem'}}
{'_id': {'Country': 'Algeria', 'City': 'Dellys'}}
{'_id': {'Country': 'Algeria', 'City': 'Ksar Chellala'}}
{'_id': {'Country': 'Algeria', 'City': 'Mansourah'}}
{'_id': {'Country': 'Algeria', 'City': 'Baghlia'}}
{'_id': {'Country': 'Algeria', 'City': 'Hennaya'}}
{'_id': {'Country': 'Algeria', 'City': 'Ain Fakroun'}}
{'_id': {'Country': 'Algeria', 'City': 'Khenchela'}}
{'_id': {'Country': 'Al

{'_id': {'Country': 'Nepal', 'City': 'Urlabari'}}
{'_id': {'Country': 'Nepal', 'City': 'Surkhet'}}
{'_id': {'Country': 'Nepal', 'City': 'Titahari'}}
{'_id': {'Country': 'Nepal', 'City': 'Gaindakot'}}
{'_id': {'Country': 'Nepal', 'City': 'Kaski'}}
{'_id': {'Country': 'Nepal', 'City': 'Bhaktapur'}}
{'_id': {'Country': 'Nepal', 'City': 'Ghorahi'}}
{'_id': {'Country': 'Nepal', 'City': 'Kathmandu'}}
{'_id': {'Country': 'Nepal', 'City': 'Pokhara'}}
{'_id': {'Country': 'Nepal', 'City': 'Kirtipur'}}
{'_id': {'Country': 'Nepal', 'City': 'Tanahun'}}
{'_id': {'Country': 'Nepal', 'City': 'Bharatpur'}}
{'_id': {'Country': 'Nepal', 'City': 'Kanchanpur'}}
{'_id': {'Country': 'Nepal', 'City': 'Dailekh'}}
{'_id': {'Country': 'Nepal', 'City': 'Patan'}}
{'_id': {'Country': 'Netherlands', 'City': 'West-Terschelling'}}
{'_id': {'Country': 'Netherlands', 'City': 'Workum'}}
{'_id': {'Country': 'Netherlands', 'City': 'Waalwijk'}}
{'_id': {'Country': 'Netherlands', 'City': 'Terheijden'}}
{'_id': {'Country': 'N

---
Unique `OS`

In [12]:
# Find all documents in the 'clicks' collection and get distinct values of 'device.OS'.
db.clicks.find().distinct('device.OS')

['Android',
 'BlackBerry OS',
 'Chrome OS',
 'Chromecast',
 'Fedora',
 'FreeBSD',
 'Kindle',
 'Linux',
 'Mac OS X',
 'NetBSD',
 'OpenBSD',
 'Other',
 'Solaris',
 'Tizen',
 'Ubuntu',
 'Windows',
 'Windows Phone',
 'iOS']

In [13]:
# Find no of  documents in the 'clicks' collection and get distinct values of 'device.OS'.
len(db.clicks.find().distinct('device.OS'))

18

---
Unique `Browser`

In [14]:
# Find all distinct values in the 'device.Browser' field from the 'clicks' collection.
db.clicks.find().distinct('device.Browser')

['AdsBot-Google',
 'AhrefsBot',
 'Amazon Silk',
 'Android',
 'AppEngine-Google',
 'Apple Mail',
 'BingPreview',
 'BlackBerry WebKit',
 'Chrome',
 'Chrome Mobile',
 'Chrome Mobile WebView',
 'Chrome Mobile iOS',
 'Chromium',
 'Coc Coc',
 'Coveobot',
 'Crosswalk',
 'Dragon',
 'DuckDuckBot',
 'Edge',
 'Edge Mobile',
 'Electron',
 'Epiphany',
 'Facebook',
 'FacebookBot',
 'Firefox',
 'Firefox Mobile',
 'Firefox iOS',
 'HbbTV',
 'HeadlessChrome',
 'HubSpot Crawler',
 'IE',
 'IE Mobile',
 'Iceweasel',
 'Iron',
 'JobBot',
 'Jooblebot',
 'K-Meleon',
 'Kindle',
 'Konqueror',
 'Magus Bot',
 'Mail.ru Chromium Browser',
 'Maxthon',
 'Mobile Safari',
 'Mobile Safari UI/WKWebView',
 'MobileIron',
 'NetFront',
 'Netscape',
 'Opera',
 'Opera Coast',
 'Opera Mini',
 'Opera Mobile',
 'Other',
 'PagePeeker',
 'Pale Moon',
 'PetalBot',
 'PhantomJS',
 'Pinterest',
 'Puffin',
 'Python Requests',
 'QQ Browser',
 'QQ Browser Mobile',
 'Radius Compliance Bot',
 'Safari',
 'Samsung Internet',
 'SeaMonkey',
 'Se

In [15]:
# Find the no of  distinct values in the 'device.Browser' field from the 'clicks' collection.
len(db.clicks.find().distinct('device.Browser'))

82

---
Unique `Activity`

In [16]:
# Retrieve all distinct values of the 'Activity' field from the 'clicks' collection
db.clicks.find().distinct('Activity')

['click', 'pageload']

----
Number of unique prodcuts

In [17]:
# Find the no of  distinct values in the 'Activity' field from the 'clicks' collection.
len(db.clicks.find().distinct('ProductID'))

10938

---
# Queries

----

----
### Q1
Get the percentage of documents where there are user ids present. Also get the percentage of documents where the user ids are absent.

***Hint - Keep total documents count in a separate variable beforehand.***

In [18]:
# Find total documents in the collection
total_docs_count = db.clicks.count_documents({})# Enter your code here
# Find the count of documents where user IDs are present
user_ids_present_count = db.clicks.count_documents({'user.UserID': {'$exists': True}})


In [19]:
cur = db.clicks.aggregate([
    # Stage 1 - check if user.UserID is absent
    {
        '$match': {'user.UserID': {'$exists': True}}
    },

    # Stage 2 - count the filtered documents
    {
        '$group': {
            '_id': 1,
            'signed_up': {'$sum': 1}
        }
    },

    # Stage 3 - find the percentage
    {
        '$project': {
            '_id':0,
            'Percentage_signed_up': {
                '$multiply':[
                    {
                        # Calculate the percentage of signed-up users
                        '$divide': ['$signed_up', total_docs_count]},  
                    100
                ] 
            },
            'Percentage_not_signed_up': {
                '$multiply': [
                    {'$divide': [
                        # Calculate the percentage of not signed-up users
                            {'$subtract': [total_docs_count,'$signed_up'] },  
                            total_docs_count
                        ]
                    },
                    100
                ]
            }
        }
    }
], allowDiskUse=True)

for doc in cur:
    pp.pprint(doc)


{'Percentage_signed_up': 9.873655737704919,
 'Percentage_not_signed_up': 90.12634426229508}


----
### Q2
What was the most popular product?

In [29]:
cur = db.clicks.aggregate([
    
            # Stage 1 - group on the ProductID field
            {
                '$group': {
                                '_id': '$ProductID',
                                'Count': {'$sum': 1}
                            }
            },
    
            # Stage 2 - sort the groups based on the Count
            {
                '$sort': {'Count': -1}
            },
    
            # Stage 3 - limit the result to return the product with the highest count
            {
                '$limit': 1
            }
        ])

for doc in cur:
    pp.pprint(doc)

{'_id': 'Pr100017', 'Count': 157922}


----
### Q3
Count the number of `click` and number of `pageload` for each signed up user. Sort the result in ascending order of the `user.UserID`.

In [21]:
cur = db.clicks.aggregate([
    # Stage 1 - Filter for signed-up users (where user.UserID is present)
    {
        '$match': {'user.UserID': {'$exists': True}}
    },

    # Stage 2 - Group by user.UserID and count clicks and pageloads
    {
        '$group': {
            '_id': '$user.UserID',
            'click_count': {
                '$sum': {'$cond': [{'$eq': ['$Activity', 'click']}, 1, 0]}
            },
            'pageload_count': {
                '$sum': {'$cond': [{'$eq': ['$Activity', 'pageload']}, 1, 0]}
            }
        }
    },

    # Stage 3 - Project to rename fields (optional)
    {
        '$project': {
            'user.UserID': '$_id',  # Renaming _id field to user.UserID
            '_id': 0,               # Excluding the default _id field from the result
            'click_count': 1,       # Including the click_count field in the result
            'pageload_count': 1     # Including the pageload_count field in the result
        }
    },

    # Stage 4 - Sort by user.UserID in ascending order
    {
        '$sort': {'user.UserID': 1}
    }
])

for doc in cur:
    pp.pprint(doc)


{'click_count': 2, 'pageload_count': 3, 'user': {'UserID': 'U100002'}}
{'click_count': 2, 'pageload_count': 2, 'user': {'UserID': 'U100003'}}
{'click_count': 11, 'pageload_count': 17, 'user': {'UserID': 'U100004'}}
{'click_count': 4, 'pageload_count': 6, 'user': {'UserID': 'U100005'}}
{'click_count': 0, 'pageload_count': 1, 'user': {'UserID': 'U100006'}}
{'click_count': 2, 'pageload_count': 4, 'user': {'UserID': 'U100007'}}
{'click_count': 39, 'pageload_count': 30, 'user': {'UserID': 'U100008'}}
{'click_count': 7, 'pageload_count': 13, 'user': {'UserID': 'U100009'}}
{'click_count': 24, 'pageload_count': 15, 'user': {'UserID': 'U100012'}}
{'click_count': 7, 'pageload_count': 10, 'user': {'UserID': 'U100013'}}
{'click_count': 13, 'pageload_count': 4, 'user': {'UserID': 'U100014'}}
{'click_count': 10, 'pageload_count': 4, 'user': {'UserID': 'U100015'}}
{'click_count': 1, 'pageload_count': 6, 'user': {'UserID': 'U100016'}}
{'click_count': 0, 'pageload_count': 1, 'user': {'UserID': 'U100017

{'click_count': 9, 'pageload_count': 5, 'user': {'UserID': 'U108248'}}
{'click_count': 0, 'pageload_count': 2, 'user': {'UserID': 'U108249'}}
{'click_count': 3, 'pageload_count': 5, 'user': {'UserID': 'U108250'}}
{'click_count': 0, 'pageload_count': 1, 'user': {'UserID': 'U108251'}}
{'click_count': 1, 'pageload_count': 7, 'user': {'UserID': 'U108252'}}
{'click_count': 0, 'pageload_count': 1, 'user': {'UserID': 'U108253'}}
{'click_count': 1, 'pageload_count': 2, 'user': {'UserID': 'U108254'}}
{'click_count': 11, 'pageload_count': 14, 'user': {'UserID': 'U108256'}}
{'click_count': 39, 'pageload_count': 1, 'user': {'UserID': 'U108257'}}
{'click_count': 0, 'pageload_count': 1, 'user': {'UserID': 'U108258'}}
{'click_count': 2, 'pageload_count': 3, 'user': {'UserID': 'U108259'}}
{'click_count': 5, 'pageload_count': 13, 'user': {'UserID': 'U108260'}}
{'click_count': 22, 'pageload_count': 8, 'user': {'UserID': 'U108261'}}
{'click_count': 14, 'pageload_count': 2, 'user': {'UserID': 'U108262'}}


{'click_count': 0, 'pageload_count': 2, 'user': {'UserID': 'U121364'}}
{'click_count': 3, 'pageload_count': 3, 'user': {'UserID': 'U121365'}}
{'click_count': 0, 'pageload_count': 1, 'user': {'UserID': 'U121366'}}
{'click_count': 26, 'pageload_count': 8, 'user': {'UserID': 'U121367'}}
{'click_count': 1, 'pageload_count': 1, 'user': {'UserID': 'U121368'}}
{'click_count': 38, 'pageload_count': 1, 'user': {'UserID': 'U121369'}}
{'click_count': 1, 'pageload_count': 1, 'user': {'UserID': 'U121371'}}
{'click_count': 2, 'pageload_count': 1, 'user': {'UserID': 'U121372'}}
{'click_count': 1, 'pageload_count': 2, 'user': {'UserID': 'U121373'}}
{'click_count': 9, 'pageload_count': 2, 'user': {'UserID': 'U121374'}}
{'click_count': 0, 'pageload_count': 1, 'user': {'UserID': 'U121375'}}
{'click_count': 1, 'pageload_count': 1, 'user': {'UserID': 'U121376'}}
{'click_count': 1, 'pageload_count': 1, 'user': {'UserID': 'U121377'}}
{'click_count': 10, 'pageload_count': 5, 'user': {'UserID': 'U121378'}}
{'c

---
### Q4
Count the number of records per `Country`. Sort the result in descending order of number of records.

In [22]:
cur = db.clicks.aggregate([
    {
        # Stage 1 - Group by user.country
        '$group': {
            '_id': '$user.Country',  # Group by user's country field
            'count': {'$sum': 1}     # Count the occurrences in each group
        }
    },
    {
        '$sort': {'count': -1}  # Sort the groups by the count field in descending order
    },
    {
        '$project': {
            'country': '$_id',  # Replace '_id' field with 'country' field in the output
            'count': 1,         # Include the 'count' field in the output
            '_id': 0            # Exclude the '_id' field from the output
        }
    }
])

for doc in cur:
    pp.pprint(doc)


{'count': 2663843, 'country': 'India'}
{'count': 833389, 'country': 'United States'}
{'count': 162125, 'country': 'United Kingdom'}
{'count': 129875, 'country': None}
{'count': 115674, 'country': 'Germany'}
{'count': 107007, 'country': 'Singapore'}
{'count': 100649, 'country': 'Canada'}
{'count': 94601, 'country': 'Australia'}
{'count': 86974, 'country': 'France'}
{'count': 86459, 'country': 'Turkey'}
{'count': 73706, 'country': 'Republic of Korea'}
{'count': 72577, 'country': 'Vietnam'}
{'count': 68222, 'country': 'Pakistan'}
{'count': 66953, 'country': 'Brazil'}
{'count': 62935, 'country': 'Malaysia'}
{'count': 57270, 'country': 'Netherlands'}
{'count': 50987, 'country': 'Italy'}
{'count': 49761, 'country': 'Spain'}
{'count': 46098, 'country': 'Indonesia'}
{'count': 46006, 'country': 'Philippines'}
{'count': 44945, 'country': 'Russia'}
{'count': 43101, 'country': 'Hong Kong'}
{'count': 40926, 'country': 'Taiwan'}
{'count': 39704, 'country': 'Poland'}
{'count': 35177, 'country': 'Chin

----
### Q5
What is the most common/frequently used `OS`? 

And, what is the most common/frequently used `Browser`? 

Also get the count for both.

In [23]:
cur = db.clicks.aggregate([
    # Stage - Sub-pipeline for each result
    {
        '$facet': {
            # Fill in the stage operator
            'most_used_os': [
                # Stage 1: Group by device OS and count occurrences
                {
                    '$group': {
                        '_id': '$device.OS',
                        'count': {'$sum': 1}
                    }
                },
                # Stage 2: Sort groups by count in descending order
                {
                    '$sort': {'count': -1}
                },
                # Stage 3: Limit to the top 1 group (most used OS)
                {
                    '$limit': 1
                },
                # Stage 4: Project the result to rename fields and exclude _id
                {
                    '$project': {
                        'Most_used_OS': '$_id',
                        'Count': '$count',
                        '_id': 0
                    }
                }
            ],
            'most_used_browser': [
                # Stage 1: Group by device browser and count occurrences
                {
                    '$group': {
                        '_id': '$device.Browser',
                        'count': {'$sum': 1}
                    }
                },
                # Stage 2: Sort groups by count in descending order
                {
                    '$sort': {'count': -1}
                },
                # Stage 3: Limit to the top 1 group (most used browser)
                {
                    '$limit': 1
                },
                # Stage 4: Project the result to rename fields and exclude _id
                {
                    '$project': {
                        'Most_used_Browser': '$_id',
                        'Count': '$count',
                        '_id': 0
                    }
                }
            ]
        }
    }
])

for doc in cur:
    pp.pprint(doc)


{'most_used_os': [{'Most_used_OS': 'Windows', 'Count': 3931349}],
 'most_used_browser': [{'Most_used_Browser': 'Chrome', 'Count': 4360498}]}


---
### Q6
What is most common `OS` and `Browser` combination used by the users? Also get the count for it.

`Example - {'Linux', 'Firefox'}`

In [24]:
cur = db.clicks.aggregate([
    # Stage 1 - Group documents by OS and Browser fields and count occurrences
    {
        '$group': {
            '_id': {
                'OS': '$device.OS', 
                'Browser': '$device.Browser'
            }, 
            'count': {'$sum': 1}
        }
    },
    
    # Stage 2 - Sort the groups in descending order based on the count
    {
        '$sort': {'count': -1}
    },
    
    # Stage 3 - Limit the result to the top 1 group (most used OS and Browser)
    {
        '$limit': 1
    },
    
    # Stage 4 - Project the result to rename fields and exclude the default _id field
    {
        '$project': {
            '_id': 0, 
            'Most_used_OS': '$_id.OS', 
            'Most_used_Browser': '$_id.Browser', 
            'Count': '$count'
        }
    }
])

# Loop through the results and print each document using pretty print (pp)
for doc in cur:
    pp.pprint(doc)


{'Most_used_OS': 'Windows', 'Most_used_Browser': 'Chrome', 'Count': 3589891}


----
### Q7
How many unique users were active in each week from  07/05/2018 - 27/05/2018?

That is, how may unique users visited in the week from 07/05/2018 - 14/05/2018, from 15/05/2018 - 21/05/2018, and so on.

***Hint - You will need the `$addToSet` operator of `$bucket` stage operator and you will need to use the `$size` aggregation operator.***

In [25]:
import datetime

# Stage 1 - filter documents for signed up users
cur = db.clicks.aggregate([
    {
        '$match': {
            'user.UserID': {'$exists': True}
        }
    },

    # Stage 2 - bucket by each week from 07/05/2018 - 27/05/2018
    {
        '$bucket': {
            'groupBy': '$VisitDateTime',
            'boundaries': [
                datetime.datetime(2018, 5, 7),
                datetime.datetime(2018, 5, 14),
                datetime.datetime(2018, 5, 21),
                datetime.datetime(2018, 5, 28)
            ],
            'output': {
                'Unique_users': {'$addToSet': '$user.UserID'}
            }
        }
    },

    # Stage 3 - project the buckets
    {
        '$project': {
            '_id': 0,
            'Week': {
                '$dateToString': {
                    'format': '%Y-%m-%d',
                    'date': '$_id'
                }
            },
            'Unique_users': {'$size': '$Unique_users'}
        }
    }
])

# Iterate and print the results
for doc in cur:
    pp.pprint(doc)


{'Week': '2018-05-07', 'Unique_users': 18308}
{'Week': '2018-05-14', 'Unique_users': 15522}
{'Week': '2018-05-21', 'Unique_users': 16636}


----
### Q8
From all the unique users who visited between 07/05/2018 - 15/05/2018 dates, who visited the most number of times? Also get a list of unique products viewed by that user in the same duration.

***Hint - Use the `$addToSet` group accumulator operator.***

In [26]:
cur = db.clicks.aggregate([
    # Stage 1 - filter the documents between the dates and where the user id exists
    {
        '$match': {
            'user.UserID': {'$exists': True},
            'VisitDateTime': {
                '$gte': datetime.datetime(2018, 5, 7),
                '$lte': datetime.datetime(2018, 5, 15)
            }
        }
    },

    # Stage 2 - group the documents on the user id,count how many times that user visited the website,
    #get an array of unique products viewed by user
    {
        '$group': {
            '_id': '$user.UserID',
            'Count': {'$sum': 1},

            # get an array of unique products viewed by the user
            'Products': {'$addToSet': '$ProductID'}
        }
    },

    # Stage 3 - sort the group by the count of visits in descending order
    {
        '$sort': {'Count': -1}
    },

    # Stage 4 - return the user who visited the most and limit the result to one document
    {
        '$limit': 1
    },
    # Stage 5: Project the result to rename fields and exclude _id
    {
        '$project': {
            'UserId':'$_id',
            '_id':0,
            'Products':1
        }
    }
])

for doc in cur:
    pp.pprint(doc)

{'Products': ['Pr100123', 'Pr100051', 'Pr100787', 'Pr100166', 'Pr100040'],
 'UserId': 'U134751'}


---
### Q9
Get the number of times each unique product was viewed by the user from the previous question in the same time duration.

In [27]:
# Perform aggregation on the 'clicks' collection using MongoDB's aggregate function.

cur = db.clicks.aggregate([
    {
        # Stage 1 - Filter documents within the specified date range: 07/05/2018 - 15/05/2018 and user ID
        '$match': {
            'VisitDateTime': {
                '$gte': datetime.datetime(2018, 5, 7),
                '$lte': datetime.datetime(2018, 5, 15)
            },
            
            # Filter documents for a specific user with UserID 'U134751'
            'user.UserID': 'U134751'
        }
    },
    {
        # Stage 2 - group the documents on the product id
        '$group': {
            # Group documents by the 'ProductID' field
            '_id': '$ProductID',
            
            # Calculate the count of documents in each group
            'Count': {'$sum': 1}
        }
    },
    {
      # Stage 3: Project the result to rename fields and exclude _id
      '$project': {
          '_id':0,
          'Product_ID': '$_id',
          'Count':1
      }
    }
])

# Iterate through the result cursor and print each document.
for doc in cur:
    pp.pprint(doc)


{'Count': 9, 'Product_ID': 'Pr100051'}
{'Count': 1393, 'Product_ID': 'Pr100166'}
{'Count': 7, 'Product_ID': 'Pr100787'}
{'Count': 33, 'Product_ID': 'Pr100123'}
{'Count': 6, 'Product_ID': 'Pr100040'}


------
### Q10
What is the last viewed product by each signed up user till 27/05/2018?

***Hint - Use the `$last` group accumulator operator.***

In [28]:

cur = db.clicks.aggregate([
    # Stage 1 - filter documents where the user id exists
    {
        '$match': {
            'user.UserID': {'$exists': True},
            'VisitDateTime': {'$lte': datetime.datetime(2018, 5, 27)}
        }
    },
    
    

    # Stage 3 - group on the user id and find the last product viewed
    {
        '$group': {
            '_id': '$user.UserID',
            'Last_product_viewed': {'$last': '$ProductID'}
        }
    },
    # Stage 2 - sort documents by user id and date of visit in descending order
    {
        '$sort': {
            '_id': 1,
            'VisitDateTime': -1
        }
    },
    {
        # Stage 3: Project the result to rename fields and exclude _id
        '$project':{
            '_id':0,
            'User_ID':'$_id',
            'Last_viewed_product':'$Last_product_viewed'
            
            
        }
    }
],
allowDiskUse=True)

for doc in cur:
    pp.pprint(doc)


{'User_ID': 'U100002', 'Last_viewed_product': 'Pr101097'}
{'User_ID': 'U100003', 'Last_viewed_product': 'Pr100178'}
{'User_ID': 'U100004', 'Last_viewed_product': 'Pr100694'}
{'User_ID': 'U100005', 'Last_viewed_product': 'Pr100430'}
{'User_ID': 'U100006', 'Last_viewed_product': 'Pr101111'}
{'User_ID': 'U100007', 'Last_viewed_product': 'Pr100209'}
{'User_ID': 'U100008', 'Last_viewed_product': 'Pr100234'}
{'User_ID': 'U100009', 'Last_viewed_product': 'Pr101070'}
{'User_ID': 'U100012', 'Last_viewed_product': 'Pr100055'}
{'User_ID': 'U100013', 'Last_viewed_product': 'Pr100015'}
{'User_ID': 'U100014', 'Last_viewed_product': 'Pr100578'}
{'User_ID': 'U100015', 'Last_viewed_product': 'Pr100390'}
{'User_ID': 'U100016', 'Last_viewed_product': 'Pr100172'}
{'User_ID': 'U100017', 'Last_viewed_product': 'Pr100119'}
{'User_ID': 'U100018', 'Last_viewed_product': 'Pr100403'}
{'User_ID': 'U100019', 'Last_viewed_product': 'Pr100179'}
{'User_ID': 'U100020', 'Last_viewed_product': 'Pr100558'}
{'User_ID': 'U

{'User_ID': 'U117776', 'Last_viewed_product': 'Pr100327'}
{'User_ID': 'U117778', 'Last_viewed_product': 'Pr100102'}
{'User_ID': 'U117779', 'Last_viewed_product': 'Pr100166'}
{'User_ID': 'U117780', 'Last_viewed_product': 'Pr100864'}
{'User_ID': 'U117781', 'Last_viewed_product': 'Pr100060'}
{'User_ID': 'U117782', 'Last_viewed_product': 'Pr100146'}
{'User_ID': 'U117783', 'Last_viewed_product': 'Pr100017'}
{'User_ID': 'U117784', 'Last_viewed_product': 'Pr101047'}
{'User_ID': 'U117785', 'Last_viewed_product': 'Pr100123'}
{'User_ID': 'U117786', 'Last_viewed_product': 'Pr100017'}
{'User_ID': 'U117787', 'Last_viewed_product': 'Pr100055'}
{'User_ID': 'U117789', 'Last_viewed_product': 'Pr100732'}
{'User_ID': 'U117790', 'Last_viewed_product': 'Pr100133'}
{'User_ID': 'U117791', 'Last_viewed_product': 'Pr100406'}
{'User_ID': 'U117792', 'Last_viewed_product': 'Pr100121'}
{'User_ID': 'U117793', 'Last_viewed_product': 'Pr100221'}
{'User_ID': 'U117794', 'Last_viewed_product': 'Pr100102'}
{'User_ID': 'U